In [ ]:
import json
import os
from typing import List
from pydantic import BaseModel, Field
from itext2kg import itext2kg_star
from itext2kg.documents_distiller import DocumentsDistiller, Article
import asyncio
from itext2kg import iText2KG_Star
from itext2kg.logging_config import setup_logging, get_logger
from itext2kg import itext2kg_star
from langchain_ollama import ChatOllama, OllamaEmbeddings
import time
from datetime import datetime

In [ ]:
# Create models for destill

In [ ]:
from typing import List, Optional
from pydantic import BaseModel, Field, field_validator
class ContentSource(BaseModel):
    name: str = Field(description="Name of the author/speaker/presenter")
    role: Optional[str] = Field(description="Role or position")
    affiliation: Optional[str] = Field(description="Organization or company affiliation")
class Content(BaseModel):
    title: str = Field(description="Title of the content (article/video)")
    sources: List[ContentSource] = Field(description="Authors/speakers involved")
    summary: str = Field(description="Brief summary of the content")
    key_concepts: List[str] = Field(description="Main concepts or topics covered")
    insights: str = Field(description="Key insights and findings")
    challenges: str = Field(description="Challenges or limitations discussed")
    solutions: str = Field(description="Proposed solutions or approaches")
    practical_applications: str = Field(description="Practical applications or implementations mentioned")

In [ ]:
# Create function for creating semantic blocks from batches (output from .py script)

In [ ]:
def load_and_create_semantic_blocks(results_dir="distilled_results"):
    """One-function solution: Load JSONs and create semantic blocks"""

    all_semantic_blocks = []

    # Get all JSON files
    json_files = [f for f in os.listdir(results_dir) if f.endswith('.json')]
    json_files.sort()  # Sort alphabetically

    print(f"Found {len(json_files)} JSON files")

    for filename in json_files:
        file_path = os.path.join(results_dir, filename)

        try:
            # Load JSON
            with open(file_path, 'r', encoding='utf-8') as f:
                json_data = json.load(f)

            # Create Content object
            content_obj = Content(**json_data)

            # Convert to semantic blocks
            for key, value in content_obj.model_dump().items():
                if value and value != [] and value != "":
                    if key == "sources" and isinstance(value, list):
                        # Handle sources list
                        sources_text = ", ".join([f"{s['name']}" for s in value if s.get('name')])
                        if sources_text:
                            block = f"{key} - {sources_text}".replace("{", "[").replace("}", "]")
                            all_semantic_blocks.append(block)
                    elif key == "key_concepts" and isinstance(value, list):
                        # Handle concepts list
                        concepts_text = ", ".join(value)
                        block = f"{key} - {concepts_text}".replace("{", "[").replace("}", "]")
                        all_semantic_blocks.append(block)
                    elif isinstance(value, str):
                        # Handle string fields
                        block = f"{key} - {value}".replace("{", "[").replace("}", "]")
                        all_semantic_blocks.append(block)

            print(f"✓ Processed {filename}")

        except Exception as e:
            print(f"✗ Error with {filename}: {e}")

    print(f"\nTotal semantic blocks created: {len(all_semantic_blocks)}")
    return all_semantic_blocks

In [ ]:
# Create semantic blocks

In [ ]:
semantic_blocks = load_and_create_semantic_blocks("vnp_itext2kg/distilled_results")

Found 28 JSON files
✓ Processed batch_1.json
✓ Processed batch_10.json
✓ Processed batch_11.json
✓ Processed batch_12.json
✓ Processed batch_13.json
✓ Processed batch_14.json
✓ Processed batch_15.json
✓ Processed batch_17.json
✓ Processed batch_18.json
✓ Processed batch_19.json
✓ Processed batch_2.json
✓ Processed batch_21.json
✓ Processed batch_22.json
✓ Processed batch_23.json
✓ Processed batch_24.json
✓ Processed batch_25.json
✓ Processed batch_26.json
✓ Processed batch_27.json
✓ Processed batch_28.json
✓ Processed batch_29.json
✓ Processed batch_3.json
✓ Processed batch_30.json
✓ Processed batch_31.json
✓ Processed batch_4.json
✓ Processed batch_5.json
✓ Processed batch_6.json
✓ Processed batch_8.json
✓ Processed batch_9.json

Total semantic blocks created: 223


In [ ]:
semantic_blocks

['title - Scrum/Agile Software Development Tools for Project Management Project Initiation in Scrum/Agile Software Development Scrum/Agile Software Development Directives Extraction',
 'sources - Scrum.org, Agile Alliance, YouTube Transcript',
 "summary - In this response, we will discuss the Scrum/Agile software development tools that are essential for project management. We will cover the key concepts, methodologies, best practices, and insights discussed in a YouTube transcript about Scrum/Agile software development. In this context, initiation tools are being discussed as part of a feasibility study for a project. The goal is to determine if the project is worthwhile and whether it's a good idea to start with the business case. This involves summarizing the current issue or problem, outlining solutions, and recommending the project. In this specific case, Billy will be working on putting together the business case, which includes creating a project charter, obtaining resources, and

In [ ]:
# Set up connection to Ollama using langchain

In [ ]:
llm_text = ChatOllama(
    model="gemma2:2b",
    temperature=0,
)
embeddings = OllamaEmbeddings(
    model="nomic-embed-text:latest",
)

In [ ]:
itext2kg_star = iText2KG_Star(llm_model=llm_text, embeddings_model=embeddings)

In [ ]:
sb = semantic_blocks[0:40]

In [ ]:
# Create graph

In [ ]:
kg = await itext2kg_star.build_graph(
    sections=sb,
    ent_threshold=0.8,
    rel_threshold=0.7,
)

[2025-08-26 13:46:16] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 1
[2025-08-26 13:46:26] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 2
[2025-08-26 13:46:35] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 3
[2025-08-26 13:47:03] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 4
[2025-08-26 13:47:37] [    INFO] [itext2kg.itext2kg.graph_matching.matcher] Relation was matched --- [Relationship_between_Product_Owner_and_Development_Team] --merged --> [Software_Development_Tool_Relationship]
[2025-08-26 13:47:37] [    INFO] [itext2kg.itext2kg.graph_matching.matcher] Relation was matched --- [Relationship_between_Key_Requirements_and_Development_Team] --merged --> [Software_Development_Tool_Relationship]
[2025-08-26 13:47:37] [    INFO] [i

In [ ]:
# Ran into blocking here, had to remove several blocks to continue (later automated in .py script)

In [ ]:
len(sb)

17

In [ ]:
len(semantic_blocks)

223

In [ ]:
13:46:16
13:58:13
11:58 min

In [ ]:
len(kg.entities)

429

In [ ]:
sb = semantic_blocks[41:47] + semantic_blocks[49:80]

In [ ]:
sb.remove(sb[16])

In [ ]:
sb.remove(sb[33])

In [ ]:
# Continue to create graph

In [ ]:
kg = await itext2kg_star.build_graph(
    sections=sb,
    ent_threshold=0.9,
    rel_threshold=0.8,
    existing_knowledge_graph=kg.model_copy(),
)

[2025-08-26 14:56:57] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 1
[2025-08-26 14:57:07] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 2
[2025-08-26 14:57:27] [    INFO] [itext2kg.itext2kg.graph_matching.matcher] Entity was matched --- [methodology:Scrum] --merged--> [software development methodology:Scrum]
[2025-08-26 14:57:27] [    INFO] [itext2kg.itext2kg.graph_matching.matcher] Relation was matched --- [Feature_of_Scrum_Agile_Software_Development] --merged --> [Relationship__Scrum_and_Agile_are_related_methodologies_in_software_development_]
[2025-08-26 14:57:27] [    INFO] [itext2kg.itext2kg.graph_matching.matcher] Relation was matched --- [Scrum_Methodology_in_Agile_Software_Development] --merged --> [Relationship__Scrum_and_Agile_are_related_methodologies_in_software_development_]
[2025-08-26 14:57:27] [    INFO] [itext2kg.itext2kg.itext2kg_star] ---

In [ ]:
sb = semantic_blocks[101:120]

In [ ]:
sb.remove(sb[9])

In [ ]:
# Continue to create graph

In [ ]:
kg = await itext2kg_star.build_graph(
    sections=sb,
    ent_threshold=0.9,
    rel_threshold=0.8,
    existing_knowledge_graph=kg.model_copy(),
)

[2025-08-26 15:46:29] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 1
[2025-08-26 15:46:42] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 2
[2025-08-26 15:47:10] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 3
[2025-08-26 15:47:38] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 4
[2025-08-26 15:47:48] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 5
[2025-08-26 15:47:56] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 6
[2025-08-26 15:48:11] [    INFO] [itext2kg.itext2kg.graph_matching.matcher] Entity was matched --- [software development process:Scrum_Agile_software_development] --merged--> [software development

In [ ]:
# Attempt to store in Neo4j

In [ ]:
from itext2kg.graph_integration import Neo4jStorage

URI = "bolt://localhost:7687"
USERNAME = "neo4j"
PASSWORD = "admin123"

# Note: Graph visualization remains synchronous
graph_integrator = Neo4jStorage(uri=URI, username=USERNAME, password=PASSWORD)
graph_integrator.visualize_graph(knowledge_graph=kg)

CypherSyntaxError: {code: Neo.ClientError.Statement.SyntaxError} {message: Invalid input '80_20_Rule': expected a node label/relationship type name, '$', '%' or '(' (line 1, column 10 (offset: 9))
"MERGE (n:80_20_Rule {name: "rule"}) SET n.embeddings = "0.0499981502,0.06644653959999999,-0.18358426,-0.030401406800000003,0.022782035200000002,0.00766889764,0.025469878600000002,0.00608047044,0.019255195200000002,-0.01572532,-0.021883343,0.028402123600000002,0.031376094,-0.00644968686,0.0332855606,-0.0166330877,-0.0187204554,-0.045099414399999996,-0.0109418124,0.01653050192,-0.0199832836,-0.0362484106,-0.039525116,-0.01325837042,0.141187064,0.0243714856,-0.0014968228000000038,-0.006360986400000001,-0.061427711600000004,-0.002482877799999998,0.00948941428,-0.0020669404,0.0361590642,-0.033189496799999996,-0.0246137606,-0.0565259652,0.07293151640000001,0.008264540800000001,0.011205588200000002,-0.0236812164,0.0310420824,0.0322139372,0.00046596460000000034,0.002924427784,-0.0007954043999999999

In [ ]:
# Save to Neo4j (Unstructured V0.1)

In [ ]:
# Ppreprocessing function (Neo4j does not support entities starting with a number)
def sanitize_node_labels(kg):
    for node in kg.entities:
        # If node label starts with a number, prefix with 'N_'
        if node.label[0].isdigit():
            node.label="N_" + node.label
        print(node)
        print("\n")
    return kg

# Apply sanitization before visualization
kg_sanitized = sanitize_node_labels(kg)
graph_integrator.visualize_graph(knowledge_graph=kg_sanitized)

label='Project_approach' name='project approach' properties=EntityProperties(embeddings=array([ 2.00312084e-02,  1.86238598e-02, -1.54179206e-01, -4.01706382e-02,
        1.29347814e-02, -1.63441010e-02,  2.58935140e-02, -3.35554564e-02,
       -3.22125628e-02,  3.70242578e-02,  3.72991220e-02, -8.49881136e-03,
        7.70653704e-02,  4.46910258e-02, -2.01025742e-02, -2.22439560e-02,
        1.12706904e-02, -6.26680160e-02, -4.54972334e-02,  2.21353700e-02,
        2.44593980e-02, -3.70186102e-02,  2.88806856e-02, -1.62740032e-02,
        1.03475774e-01, -5.36636037e-03, -1.40473782e-02, -1.12636489e-02,
       -4.53472092e-03, -5.04384020e-03,  1.27913800e-02, -4.10469700e-02,
       -1.60941062e-03, -7.22077616e-04, -2.93573764e-02, -7.45512720e-02,
        3.39461332e-02,  2.63852712e-02, -3.57755408e-02, -5.29985280e-02,
       -3.86579160e-02, -1.17407898e-02, -1.16858118e-03, -5.49015006e-02,
        1.22921772e-02, -4.43401016e-02,  3.52799586e-02, -9.74585520e-03,
        3.08

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [ ]:
sb = semantic_blocks[121:140]

In [ ]:
sb.remove(sb[5])

In [ ]:
# Continue to create graph

In [ ]:
kg = await itext2kg_star.build_graph(
    sections=sb,
    ent_threshold=0.9,
    rel_threshold=0.8,
    existing_knowledge_graph=kg.model_copy(),
)

[2025-08-26 16:06:13] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 1
[2025-08-26 16:06:21] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 2
[2025-08-26 16:06:41] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 3
[2025-08-26 16:07:03] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 4
[2025-08-26 16:07:22] [    INFO] [itext2kg.itext2kg.graph_matching.matcher] Entity was matched --- [scrum agile software development:Scrum_Agile_Software_Development] --merged--> [scrum/agile software development:Scrum_Agile_software_development]
[2025-08-26 16:07:22] [    INFO] [itext2kg.itext2kg.graph_matching.matcher] Relation was matched --- [relationship_2__Insights_and_Fish_Bone_Diagrams] --merged --> [Relationship_between_Opportunity_Analysis_and_Fish_B

In [ ]:
sb = semantic_blocks[141:160]

In [ ]:
sb.remove(sb[12])

In [ ]:
# Continue to create graph

In [ ]:
kg = await itext2kg_star.build_graph(
    sections=sb,
    ent_threshold=0.9,
    rel_threshold=0.8,
    existing_knowledge_graph=kg.model_copy(),
)

[2025-08-26 16:20:09] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 1
[2025-08-26 16:20:25] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 2
[2025-08-26 16:20:50] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 3
[2025-08-26 16:21:04] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 4
[2025-08-26 16:21:14] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 5
[2025-08-26 16:21:19] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 6
[2025-08-26 16:21:42] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 7
[2025-08-26 16:21:54] [    INFO] [itext2kg.itext2kg.graph_matc

In [ ]:
sb = semantic_blocks[161:180]

In [ ]:
# Continue to create graph

In [ ]:
kg = await itext2kg_star.build_graph(
    sections=sb,
    ent_threshold=0.9,
    rel_threshold=0.8,
    existing_knowledge_graph=kg.model_copy(),
)

[2025-08-26 16:28:22] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 1
[2025-08-26 16:28:38] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 2
[2025-08-26 16:29:00] [    INFO] [itext2kg.itext2kg.graph_matching.matcher] Entity was matched --- [scrum/agile:Agile_development] --merged--> [scrum/agile software development:Scrum_Agile_Software_Development]
[2025-08-26 16:29:00] [    INFO] [itext2kg.itext2kg.graph_matching.matcher] Entity was matched --- [stakeholder matrix:key_concepts] --merged--> [stakeholder matrix:Stakeholder_Matrix]
[2025-08-26 16:29:00] [    INFO] [itext2kg.itext2kg.graph_matching.matcher] Relation was matched --- [Relationship_5__Stakeholder_Matrix_and_Success_in_Agile_Project] --merged --> [Relationship__Stakeholder_Matrix_to_Project_Impact_and_Influence]
[2025-08-26 16:29:00] [    INFO] [itext2kg.itext2kg.graph_matching.matcher] Relation was 

In [ ]:
sb = semantic_blocks[181:200]

In [ ]:
sb.remove(sb[12])

In [ ]:
# Continue to create graph

In [ ]:
kg = await itext2kg_star.build_graph(
    sections=sb,
    ent_threshold=0.9,
    rel_threshold=0.8,
    existing_knowledge_graph=kg.model_copy(),
)

[2025-08-26 16:46:54] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 1
[2025-08-26 16:47:09] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 2
[2025-08-26 16:47:23] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 3
[2025-08-26 16:47:30] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 4
[2025-08-26 16:47:38] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 5
[2025-08-26 16:48:06] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 6
[2025-08-26 16:48:56] [    INFO] [itext2kg.itext2kg.graph_matching.matcher] Entity was matched --- [stakeholder engagement matrix:Stakeholder_Engagement_Matrix] --merged--> [stakeholderengagementm

In [ ]:
sb = semantic_blocks[201:222]

In [ ]:
sb.remove(sb[19])

In [ ]:
# Continue to create graph

In [ ]:
kg = await itext2kg_star.build_graph(
    sections=sb,
    ent_threshold=0.9,
    rel_threshold=0.8,
    existing_knowledge_graph=kg.model_copy(),
)

[2025-08-26 17:03:35] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 1
[2025-08-26 17:04:14] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 2
[2025-08-26 17:04:26] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 3
[2025-08-26 17:04:46] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 4
[2025-08-26 17:04:55] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 5
[2025-08-26 17:05:04] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 6
[2025-08-26 17:05:10] [    INFO] [itext2kg.itext2kg.itext2kg_star] ------- Extracting Relations and Deriving Entities from Document 7
[2025-08-26 17:05:18] [    INFO] [itext2kg.itext2kg.graph_matc

In [ ]:
# Save to Neo4j (Unstructured V0.2)

In [ ]:
# Preprocessing function
def sanitize_node_labels(kg):
    for node in kg.entities:
        # If node label starts with a number, prefix with 'N_'
        if node.label[0].isdigit():
            node.label="N_" + node.label
        print(node)
        print("\n")
    return kg

# Apply sanitization before visualization
kg_sanitized = sanitize_node_labels(kg)
graph_integrator.visualize_graph(knowledge_graph=kg_sanitized)

label='Project_approach' name='project approach' properties=EntityProperties(embeddings=array([ 2.00312084e-02,  1.86238598e-02, -1.54179206e-01, -4.01706382e-02,
        1.29347814e-02, -1.63441010e-02,  2.58935140e-02, -3.35554564e-02,
       -3.22125628e-02,  3.70242578e-02,  3.72991220e-02, -8.49881136e-03,
        7.70653704e-02,  4.46910258e-02, -2.01025742e-02, -2.22439560e-02,
        1.12706904e-02, -6.26680160e-02, -4.54972334e-02,  2.21353700e-02,
        2.44593980e-02, -3.70186102e-02,  2.88806856e-02, -1.62740032e-02,
        1.03475774e-01, -5.36636037e-03, -1.40473782e-02, -1.12636489e-02,
       -4.53472092e-03, -5.04384020e-03,  1.27913800e-02, -4.10469700e-02,
       -1.60941062e-03, -7.22077616e-04, -2.93573764e-02, -7.45512720e-02,
        3.39461332e-02,  2.63852712e-02, -3.57755408e-02, -5.29985280e-02,
       -3.86579160e-02, -1.17407898e-02, -1.16858118e-03, -5.49015006e-02,
        1.22921772e-02, -4.43401016e-02,  3.52799586e-02, -9.74585520e-03,
        3.08

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



label='frequency' name='twice a week' properties=EntityProperties(embeddings=array([-5.83171000e-03,  2.66235356e-02, -1.91138094e-01, -3.27898112e-02,
        1.20154743e-02, -3.88019198e-02,  1.43131552e-02, -2.43655512e-02,
        1.81544708e-02, -4.18990820e-02, -2.49128508e-02,  2.60779722e-02,
        1.57822764e-02,  2.86135212e-02, -2.94753872e-02, -9.68494712e-03,
       -2.65395820e-02, -1.88610944e-02, -2.04827548e-02,  4.24140602e-02,
       -2.06525208e-02,  1.68638032e-02,  3.97482220e-03, -3.54495468e-02,
        6.70778680e-02,  7.36709108e-02,  1.01457185e-02,  9.33145400e-04,
       -9.86863268e-03,  2.69537264e-02, -1.26503088e-02,  6.09471644e-03,
        1.75061198e-02, -4.50820120e-02, -3.32991344e-03, -2.35612138e-02,
        5.04586980e-03, -1.50594570e-02,  5.86159940e-03,  7.04553840e-03,
        2.47052448e-02,  3.93341780e-03,  1.77562936e-02, -2.47694505e-02,
        3.37569976e-02, -5.49528586e-02,  1.00583128e-02,  5.69569760e-02,
        1.00839386e-02,